# Скрипт для сравнения содержания лекции в разных ветках

Данный скрипт предназначен для того, чтобы упростить Вам жизнь, если Вы хотите сравнить содержание лекции в рамках двух ветвей и оценить изменения. Скрипт учитывает то, что лекции меняются местами, поэтому номер лекции нужно задать отдельно для каждой ветки. В результате работы скрипта Вы получите выходной файл `output.xlsx`.

Импортируем все необходимые библиотеки:

In [ ]:
import re
import json
import base64
import requests
import pandas as pd
from bs4 import BeautifulSoup

Введите номера бранчей и номер нужной лекции от $1$ до $15$ в каждой из них, а также свой Github Access Token. Если Вы не знаете, что это и как его создать, смотрите [инструкцию по использованию скриптов](https://ximc.ru/projects/edunet/wiki/%D0%98%D0%BD%D1%81%D1%82%D1%80%D1%83%D0%BA%D1%86%D0%B8%D1%8F_%D0%BF%D0%BE_%D0%B8%D1%81%D0%BF%D0%BE%D0%BB%D1%8C%D0%B7%D0%BE%D0%B2%D0%B0%D0%BD%D0%B8%D1%8E_%D1%81%D0%BA%D1%80%D0%B8%D0%BF%D1%82%D0%BE%D0%B2/edit#%D0%9F%D1%80%D0%BE-Github-Access-Token-%D0%B8-GitLab-Access-Token).

In [ ]:
dev_branch_1 = "dev-2.0"
dev_branch_2 = "dev-1.9"
lection_num_1 = 2
lection_num_2 = 2
github_token = "Input Your GitHub Access Token Here"

Так как из репозитория можно получить имена файлов только из дефолтной ветки, а Вам может понадобиться получить содержание лекции из какой-то другой, названия лекций вручную заданы. Список `lectures_names_1` соответствует названиям лекций в dev-1.9 и dev-1.10, а lectures_names_2 соответствует названиям лекций в dev-2.0.

In [ ]:
lectures_names_1 = ['L01_Intro.ipynb', 'L02_Linear_classifier.ipynb', 'L03_Classic_ML.ipynb', 'L04_Feature_Engineering.ipynb', 'L05_Neural_networks.ipynb', 'L06_CNN.ipynb', 'L07_Batch_normalization.ipynb', 'L08_RNN.ipynb', 'L09_CNN_Architectures.ipynb', 'L10_Explainability.ipynb', 'L11_Learning_on_Real_data.ipynb', 'L12_Segmentation_Detection.ipynb', 'L13_Autoencoders.ipynb', 'L14_GAN_cGAN.ipynb', 'L15_RL.ipynb']
lectures_names_2 = ['L01_Intro.ipynb', 'L02_Linear_models.ipynb', 'L03_Classic_ML.ipynb', 'L04_Feature_Engineering.ipynb', 'L05_Neural_networks.ipynb', 'L06_CNN.ipynb', 'L07_Learning_techniques.ipynb', 'L08_NN_architectures.ipynb', 'L09_RNN.ipynb', 'L10_Transformers.ipynb', 'L11_Segmentation_Detection.ipynb', 'L12_Representation_learning.ipynb', 'L13_Generative_models.ipynb', 'L14_Explainability.ipynb', 'L15_RL.ipynb']

Работаем с первой веткой

In [ ]:
headers = {}
cpattern = re.compile(r"```[^`]*?```")        # code pattern in markdown
headers_h1 = []
headers_h2 = []

if github_token:
    headers['Authorization'] = f"token {github_token}"

if (dev_branch_1 == 'dev-2.0'):
    lecture = lectures_names_2[lection_num_1-1]
else:
    lecture = lectures_names_1[lection_num_1-1]

url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_branch_1}'
r = requests.get(url, headers=headers)
r.raise_for_status()
data = r.json()
file_content = data['content']
file_content_encoding = data.get('encoding')
if file_content_encoding == 'base64':
    file_content = base64.b64decode(file_content).decode()
file_content = json.loads(file_content)


for cell in file_content["cells"]:
    if cell["cell_type"] == "markdown":
        s = "".join(cell["source"])
        s = cpattern.sub("", s)

        for source in s.split("\n"):
            source = cpattern.sub("", source)

            if ("# " == source[0:2]):
                headers_h1.append(source[2:])
                headers_h2.append(" ")
            if("## " in source[0:3]):
                headers_h2.append(source[3:])
                headers_h1.append(" ")

df_1 = pd.DataFrame(data={dev_branch_1: headers_h2}, index=headers_h1)

Работаем со второй веткой:

In [ ]:
cpattern = re.compile(r"```[^`]*?```")        # code pattern in markdown
headers = {}
headers_h1 = []
headers_h2 = []

if github_token:
    headers['Authorization'] = f"token {github_token}"

if (dev_branch_2 == 'dev-2.0'):
    lecture = lectures_names_2[lection_num_2-1]
else:
    lecture = lectures_names_1[lection_num_2-1]

url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_branch_2}'
r = requests.get(url, headers=headers)
r.raise_for_status()
data = r.json()
file_content = data['content']
file_content_encoding = data.get('encoding')
if file_content_encoding == 'base64':
    file_content = base64.b64decode(file_content).decode()
file_content = json.loads(file_content)


for cell in file_content["cells"]:
    if cell["cell_type"] == "markdown":
        s = "".join(cell["source"])
        s = cpattern.sub("", s)

        for source in s.split("\n"):
            source = cpattern.sub("", source)

            if ("# " == source[0:2]):
                headers_h1.append(source[2:])
                headers_h2.append(" ")
            if("## " in source[0:3]):
                headers_h2.append(source[3:])
                headers_h1.append(" ")


df_2 = pd.DataFrame(data={dev_branch_2: headers_h2}, index=headers_h1)

Записываем результат в выходной файл:

In [ ]:
with pd.ExcelWriter("output.xlsx") as writer:
    df_1.to_excel(writer, sheet_name="Sheet1")
    df_2.to_excel(writer, sheet_name="Sheet1", startcol=2)

Теперь Вы можете скачать получившийся файл `output.xlsx` в папке `Файлы` в меню слева. Первые два столбца будут соответствовать заголовком уровня H1, H2 в первом бранче, вторые два столбца — во втором.